In [4]:
!pip uninstall fastai
!pip install fastai

Uninstalling fastai-2.1.8:
  Would remove:
    /usr/local/lib/python3.6/dist-packages/fastai-2.1.8.dist-info/*
    /usr/local/lib/python3.6/dist-packages/fastai/*
Proceed (y/n)? y
  Successfully uninstalled fastai-2.1.8
  Using cached https://files.pythonhosted.org/packages/ff/53/da994550c0dd2962351fd694694e553afe0c9516c02251586790f830430b/fastai-2.1.8-py3-none-any.whl


In [36]:
from fastai import *
from fastai.tabular import *
from fastai.tabular.all import *
from fastai.collab import *
import numpy as np
import pandas as pd
from pathlib import Path

In [37]:
path = Path('')

df = pd.read_csv(path/'train_pca_var.csv')
test = pd.read_csv(path/'test_pca_var.csv')
df['Culture']-=1
df

0         1         2  ...       111       112  Culture
0     4.644999 -1.171835 -0.081057  ... -0.000521 -0.001490        3
1    -2.485984 -0.186353 -1.274751  ...  0.000973  0.012880       16
2    -2.730865 -0.298112  0.203354  ... -0.001310  0.000063        1
3     3.204312 -0.274076  0.840615  ... -0.000422  0.000083        3
4    -2.360852  1.509807 -1.100292  ... -0.001085  0.001010        3
...        ...       ...       ...  ...       ...       ...      ...
2823  3.370614 -0.443714  0.743663  ... -0.001597  0.000350        3
2824  2.034094  0.137510 -1.211978  ...  0.000643  0.000546        3
2825  1.537344  0.073370 -0.965067  ...  0.000679  0.001045        3
2826 -1.134091  1.653277  0.014823  ... -0.000670 -0.000755        4
2827 -0.684781 -1.131790  0.703278  ... -0.001341 -0.000191        6

[2828 rows x 114 columns]

In [40]:
CONT_NAMES = list((df.drop(['Culture'],axis=1)).columns)
TARGET='Culture'

df[TARGET] = df[TARGET].astype('category')

In [59]:
class_count_df = df.groupby(TARGET).count()
classes=pd.Series(list(class_count_df['0']))
new_weights=[]
for i in classes:
    new_weights.append((classes.sum()) / (2.0 * i))
class_weights=torch.FloatTensor(new_weights)

In [74]:
def seed_everything(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

In [75]:
metrics = F1Score(average='weighted')
loss_func = CrossEntropyLossFlat(weight=class_weights)
for j in [0,15,42,96,154,80]:
  seed_everything(seed=j)
  splits = RandomSplitter(valid_pct=0.19)(range_of(df))
  dls = TabularDataLoaders.from_df(df, 
                                 y_names=TARGET,
                                 splits=splits)
  learn = tabular_learner(dls,layers=[1000,2500], loss_func=loss_func,metrics=[metrics])
  learn.fit_one_cycle(n_epoch=16,wd=0.001)
  rows=[]
  for i in test.index:
    row, clas, probs=learn.predict(test.iloc[i])
    rows.append(row['Culture'][0])
  rows=np.asarray(rows)
  rows+=1
  pd.Series(rows).to_csv('fastai'+str(j)+'.csv', index=False, header=['Culture'])

In [76]:
metrics = F1Score(average='weighted')
loss_func = CrossEntropyLossFlat(weight=class_weights)
for j in [1,7,6,99,854,666,482,123465,123456,70]:
  seed_everything(seed=j)
  splits = RandomSplitter(valid_pct=0.19)(range_of(df))
  dls = TabularDataLoaders.from_df(df, 
                                 y_names=TARGET,
                                 splits=splits)
  learn = tabular_learner(dls,layers=[1000,2500], loss_func=loss_func,metrics=[metrics])
  learn.fit_one_cycle(n_epoch=16,wd=0.001)
  rows=[]
  for i in test.index:
    row, clas, probs=learn.predict(test.iloc[i])
    rows.append(row['Culture'][0])
  rows=np.asarray(rows)
  rows+=1
  pd.Series(rows).to_csv('fastai'+str(j)+'.csv', index=False, header=['Culture'])